LAST LINKs:
* https://colab.research.google.com/drive/1WIk2bxglElfZewOHboPFNj8H44_VAyKE?usp=sharing#scrollTo=Gw3IZYrfKl4Z
* https://medium.com/analytics-vidhya/fine-tune-a-roberta-encoder-decoder-model-trained-on-mlm-for-text-generation-23da5f3c1858
* https://huggingface.co/course/chapter7/7?fw=tf

LINKs:
* https://github.com/huggingface/notebooks/blob/main/examples/question_answering.ipynb

* https://github.com/Michael-M-Mike/Unibo-NLP-Assignments/blob/main/A2_Seq2Seq_Abstractive_Question_Answering_(QA)_on_CoQA/distilroberta_42.ipynb

# Assignment 2

**Credits**: Andrea Galassi, Federico Ruggeri, Paolo Torroni

**Keywords**: Transformers, Question Answering, CoQA

## Overview

### Problem

Question Answering (QA) on [CoQA](https://stanfordnlp.github.io/coqa/) dataset: a conversational QA dataset.

### Task

Given a question $Q$, a text passage $P$, the task is to generate the answer $A$.<br>
$\rightarrow A$ can be: (i) a free-form text or (ii) unanswerable;

**Note**: an question $Q$ can refer to previous dialogue turns. <br>
$\rightarrow$ dialogue history $H$ may be a valuable input to provide the correct answer $A$.

### Models

We are going to experiment with transformer-based models to define the following models:

1.  $A = f_\theta(Q, P)$

2. $A = f_\theta(Q, P, H)$

where $f_\theta$ is the transformer-based model we have to define with $\theta$ parameters.

## The CoQA dataset

<center>
    <img src="https://drive.google.com/uc?export=view&id=16vrgyfoV42Z2AQX0QY7LHTfrgektEKKh" width="750"/>
</center>

For detailed information about the dataset, feel free to check the original [paper](https://arxiv.org/pdf/1808.07042.pdf).



## Rationales

Each QA pair is paired with a rationale $R$: it is a text span extracted from the given text passage $P$. <br>
$\rightarrow$ $R$ is not a requested output, but it can be used as an additional information at training time!

## Dataset Statistics

* **127k** QA pairs.
* **8k** conversations.
* **7** diverse domains: Children's Stories, Literature, Mid/High School Exams, News, Wikipedia, Reddit, Science.
* Average conversation length: **15 turns** (i.e., QA pairs).
* Almost **half** of CoQA questions refer back to **conversational history**.
* Only **train** and **validation** sets are available.

## Dataset snippet

The dataset is stored in JSON format. Each dialogue is represented as follows:

```
{
    "source": "mctest",
    "id": "3dr23u6we5exclen4th8uq9rb42tel",
    "filename": "mc160.test.41",
    "story": "Once upon a time, in a barn near a farm house, there lived a little white kitten named Cotton. 
    Cotton lived high up in a nice warm place above the barn where all of the farmer's horses slept. [...]" % <-- $P$
    "questions": [
        {
            "input_text": "What color was Cotton?",   % <-- $Q_1$
            "turn_id": 1
        },
        {
            "input_text": "Where did she live?",
            "turn_id": 2
        },
        [...]
    ],
    "answers": [
        {
            "span_start": 59,   % <-- $R_1$ start index
            "spand_end": 93,    % <-- $R_1$ end index
            "span_text": "a little white kitten named Cotton",   % <-- $R_1$
            "input_text" "white",   % <-- $A_1$      
            "turn_id": 1
        },
        [...]
    ]
}
```

### Simplifications

Each dialogue also contains an additional field ```additional_answers```. For simplicity, we **ignore** this field and only consider one groundtruth answer $A$ and text rationale $R$.

CoQA only contains 1.3% of unanswerable questions. For simplicity, we **ignore** those QA pairs.

# [0] Functions and imports

In [1]:
# %%capture
# !pip install datasets
# !pip install transformers
# !pip install tensorflow_addons
# !pip install allennlp-models


# NOTE:
#     - SEED ED ERRORE
#     - LUNGHEZZA INPUTS E OUTPUTS - https://towardsdatascience.com/to-distil-or-not-to-distil-bert-roberta-and-xlnet-c777ad92f8
#     - GRANDEZZA DATASETS
#     - WARNINGS NELLA CREAZIONE DEL MODELLO E NEL TRAINING
#     - COME UTILIZZARE SPAN DI TESTO

In [22]:
from IPython.display import display_html, clear_output
from itertools import chain,cycle
import plotly.express as px
from copy import deepcopy
import urllib.request
import transformers
import numpy as np
import json
import time
import os
import torch
import random 
import warnings
import pandas as pd
from tqdm import tqdm

from sklearn.model_selection import GroupShuffleSplit
from datasets import *
from transformers import AutoTokenizer, PreTrainedTokenizerFast, EncoderDecoderModel, Seq2SeqTrainingArguments, Seq2SeqTrainer, AdamW, DataCollatorForSeq2Seq

# warnings.filterwarnings(action='once')    
warnings.filterwarnings(action='ignore')

os.environ['TOKENIZERS_PARALLELISM'] = 'true'

# Display dataframes 
def display(*args,titles=cycle([''])):
    html_str=''
    for df,title in zip(args, chain(titles,cycle(['</br>'])) ):
        html_str+='<th style="text-align:left"><td style="vertical-align:top">'
        html_str+=f'<h4 style="text-align: left;">{title}</h2>'
        html_str+=df.to_html().replace('table','table style="display:inline"')
        html_str+='</td></th>'
    display_html(html_str,raw=True)
    
# Setting seeds for reproducibility
def set_reproducibility(seed):
    random.seed(seed)
    np.random.seed(seed)
    torch.manual_seed(seed)
    torch.cuda.manual_seed(seed)
    transformers.set_seed(seed)
    torch.backends.cudnn.benchmark = False
    torch.backends.cudnn.deterministic = True

    os.environ['TF_DETERMINISTIC_OPS'] = '1'

# Check tokenizer special tokens
def check_tokens(tokenizer):
    # Get the special tokens and their corresponding IDs
    special_tokens = tokenizer.special_tokens_map
    special_ids = tokenizer.convert_tokens_to_ids(list(special_tokens.values()))
    print("Special tokens:")
    for token_type, token_list in special_tokens.items():
        print(f"{token_type}: {token_list}")
    # Print the special tokens and their corresponding IDs
    for token, id in zip(special_tokens.keys(), special_ids):
        print(f"{token}: {id}")
        
# Compute metrics in the trainer
def compute_metrics(pred,tokenizer):
    labels = pred.label_ids
    preds = pred.predictions
    
    labels_text = tokenizer.batch_decode(labels, skip_special_tokens=True)
    preds_text = tokenizer.batch_decode(preds, skip_special_tokens=True)
    
    squad_scores=[]
    for i in range(len(preds_text)):
        squad_scores.append(compute_f1(str(preds_text[i]), str(labels_text[i])))
    mean_squad_f1 = sum(squad_scores)/len(squad_scores)

    return {"squad_f1_score": mean_squad_f1}

# Generate Answers
def generate_answers(test_loader,model,tokenizer,dataset,verbose=False):
    i=0
    generated_answers = []
    squad_scores = []
    for batch in tqdm(test_loader):
        

        example = batch['input_ids'].to(device)
        att_mask = batch['attention_mask'].to(device)
        generated_ids = model.generate(input_ids=example, 
                                          attention_mask=att_mask,
                                          max_length=max_length_answer
                                         )
        

        generated_answer = tokenizer.batch_decode(generated_ids, skip_special_tokens=True)
        ground_truth = dataset['answer'][i:i+batch_size]
        
        
        squad = []
        for j in range(len(generated_answer)):                
            sq = compute_f1(generated_answer[j], ground_truth[j])
            generated_answers.append(generated_answer[j])
            squad_scores.append(sq)
            squad.append(sq)
                

        if verbose:
            print(dataset['question'][i:i+batch_size])
            print(f'Generated ans: {generated_answer}')
            print(f'True ans: {ground_truth}')
            print(f'SQuAD F1 score: {squad}')
            
#        for idx in range(batch_size):
#          for idx in range(int(batch_size/4)):
#             print(f'Question: [{dataset["test"]["question"][i+idx]}]')
#             print(f'\tGT: {ground_truth[idx]}\t-\tGENERATED: {generated_answers[idx]}')
        i+=batch_size  
            
            
    mean_squad_f1 = sum(squad_scores)/len(squad_scores)
    print(f'Mean SQuAD F1-score: {mean_squad_f1}')   
    
    dataset = dataset.add_column("generated_answer", generated_answers)
    dataset = dataset.add_column("squad_score", squad_scores)

    return dataset
        
# Add history to context    
def add_history_to_context(df):
    print('Adding the history to each entry of the dataframe...')
    # Sort the dataframe by 'id' and 'turn_id'
    df = df.sort_values(['id', 'turn_id'])
    # Group the dataframe by 'id'
    groups = df.groupby('id')
    # Create an empty list to store the updated rows
    new_rows = []
    # Iterate over each group
    for _, group in tqdm(groups):
        # Initialize an empty string for the history 
        history = ''
        # Iterate over each row in the group
        for i, row in group.iterrows():
            # Concatenate 'input_text_x' and 'input_text_y' for each row
            if row['turn_id'] > 1: # only consider previous turn_ids
                prev_rows = group.loc[group['turn_id'] < row['turn_id'], ['input_text_x', 'input_text_y']]
                history = ''.join(prev_rows['input_text_x'] + prev_rows['input_text_y'] + ';')
            else:
                history = ''
            # Update the 'history_context' column for the current row
            new_row = row.copy()
            if history == '':
                new_row['history_context'] = row['story']
            else:
                new_row['history_context'] = history+'</s>'+row['story']
            # Append the updated row to the list of new rows
            new_rows.append(new_row)
    # Create a new dataframe with the updated rows
    result_df = pd.DataFrame(new_rows)
    print('History added.')
    return result_df
# Show the worst 5 preds per source
def show_worst_five(dataset):
    df = pd.DataFrame(dataset)
    
    for source in df['source'].unique():
        source_df = df[df['source'] == source]
        sorted_df = source_df.sort_values(by='squad_score', ascending=True)
        worst_5_df = sorted_df.head(5)
        print(f"Source: {source}")
        display(worst_5_df[['context', 'question', 'answer', 'generated_answer', 'squad_score']])
        print()
   
load_model = False

In [3]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")     

print("Using device:", device)

Using device: cuda


In [4]:
!nvidia-smi

Wed Mar 29 13:54:35 2023       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 528.49       Driver Version: 528.49       CUDA Version: 12.0     |
|-------------------------------+----------------------+----------------------+
| GPU  Name            TCC/WDDM | Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  NVIDIA GeForce ... WDDM  | 00000000:01:00.0 Off |                  N/A |
| N/A   47C    P0    33W / 125W |      0MiB /  8192MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

### SQuAD metric

In [5]:
"""
https://github.com/allenai/allennlp-models/blob/main/allennlp_models/rc/tools/squad.py

Functions taken from [the official evaluation script]
(https://worksheets.codalab.org/rest/bundles/0x6b567e1cf2e041ec80d7098f031c5c9e/contents/blob/)
for SQuAD version 2.0.
"""
import collections
import re
import string
from typing import Callable, Sequence, TypeVar, Tuple


def make_qid_to_has_ans(dataset):
    qid_to_has_ans = {}
    for article in dataset:
        for p in article["paragraphs"]:
            for qa in p["qas"]:
                qid_to_has_ans[qa["id"]] = bool(qa["answers"])
    return qid_to_has_ans


def normalize_answer(s):
    """Lower text and remove punctuation, articles and extra whitespace."""

    def remove_articles(text):
        regex = re.compile(r"\b(a|an|the)\b", re.UNICODE)
        return re.sub(regex, " ", text)

    def white_space_fix(text):
        return " ".join(text.split())

    def remove_punc(text):
        exclude = set(string.punctuation)
        return "".join(ch for ch in text if ch not in exclude)

    def lower(text):
        return text.lower()

    return white_space_fix(remove_articles(remove_punc(lower(s))))


def get_tokens(s):
    if not s:
        return []
    return normalize_answer(s).split()


def compute_exact(a_pred: str, a_gold: str) -> int:
    return int(normalize_answer(a_pred) == normalize_answer(a_gold))


def compute_f1(a_pred: str, a_gold: str) -> float:
    pred_toks = get_tokens(a_pred)
    gold_toks = get_tokens(a_gold)
    common = collections.Counter(pred_toks) & collections.Counter(gold_toks)  # type: ignore[var-annotated]
    num_same = sum(common.values())
    if len(pred_toks) == 0 or len(gold_toks) == 0:
        # If either is no-answer, then F1 is 1 if they agree, 0 otherwise
        return float(pred_toks == gold_toks)
    if num_same == 0:
        return 0.0
    precision = 1.0 * num_same / len(pred_toks)
    recall = 1.0 * num_same / len(gold_toks)
    f1 = (2 * precision * recall) / (precision + recall)
    return f1


_P = TypeVar("_P")
_G = TypeVar("_G")
_T = TypeVar("_T", int, float, Tuple[int, ...], Tuple[float, ...])


def metric_max_over_ground_truths(
    metric_fn: Callable[[_P, _G], _T], prediction: _P, ground_truths: Sequence[_G]
) -> _T:
    scores_for_ground_truths = []
    for ground_truth in ground_truths:
        score = metric_fn(prediction, ground_truth)
        scores_for_ground_truths.append(score)
    return max(scores_for_ground_truths)


def get_metric_score(prediction: str, gold_answers: Sequence[str]) -> Tuple[int, float]:
    exact_scores = metric_max_over_ground_truths(compute_exact, prediction, gold_answers)
    f1_scores = metric_max_over_ground_truths(compute_f1, prediction, gold_answers)
    return exact_scores, f1_scores

## [Task 1] Remove unaswerable QA pairs

Write your own script to remove unaswerable QA pairs from both train and validation sets.

## Dataset Download


In [6]:
class DownloadProgressBar(tqdm):
    def update_to(self, b=1, bsize=1, tsize=None):
        if tsize is not None:
            self.total = tsize
        self.update(b * bsize - self.n)
        
def download_url(url, output_path):
    with DownloadProgressBar(unit='B', unit_scale=True,
                             miniters=1, desc=url.split('/')[-1]) as t:
        urllib.request.urlretrieve(url, filename=output_path, reporthook=t.update_to)

def download_data(data_path, url_path, suffix):    
    if not os.path.exists(data_path):
        os.makedirs(data_path)
        
    data_path = os.path.join(data_path, f'{suffix}.json')

    if not os.path.exists(data_path):
        print(f"Downloading CoQA {suffix} data split... (it may take a while)")
        download_url(url=url_path, output_path=data_path)
        urllib.request.urlretrieve(url_path, filename=data_path)
        print("Download completed!")

In [7]:
# Train data
train_url = "https://nlp.stanford.edu/data/coqa/coqa-train-v1.0.json"
download_data(data_path='coqa', url_path=train_url, suffix='train')

# Test data
test_url = "https://nlp.stanford.edu/data/coqa/coqa-dev-v1.0.json"
download_data(data_path='coqa', url_path=test_url, suffix='test')  # <-- Why test? See next slides for an answer!

#### Data Inspection

Spend some time in checking accurately the dataset format and how to retrieve the tasks' inputs and outputs!

In [8]:
# Creating Dataframes and removing unanswerable questions
train_data = json.load((open('coqa/train.json')))
test_data = json.load((open('coqa/test.json')))

qas = pd.json_normalize(train_data['data'], ['questions'], ['source', 'id', 'story'])
ans = pd.json_normalize(train_data['data'], ['answers'],['id'])
train_val_df = pd.merge(qas,ans, left_on=['id','turn_id'], right_on=['id','turn_id'])
train_val_df = train_val_df.loc[train_val_df['input_text_y']!='unknown']

qas = pd.json_normalize(test_data['data'], ['questions'], ['source', 'id', 'story'])
ans = pd.json_normalize(test_data['data'], ['answers'],['id'])
test_df = pd.merge(qas,ans, left_on=['id','turn_id'], right_on=['id','turn_id'])
test_df = test_df.loc[test_df['input_text_y']!='unknown']

In [9]:
# Removing bad turns
train_val_df = train_val_df.loc[(train_val_df['bad_turn_x'] != 'True') & (train_val_df['bad_turn_y'] != 'True')]

# Removing equal text/answer entries
train_val_df = train_val_df[train_val_df.story != train_val_df.input_text_y]
test_df = test_df[test_df.story != test_df.input_text_y]

# Removing enties with empty answers
train_val_df = train_val_df[train_val_df['input_text_y'].str.len()>0]
test_df = test_df[test_df['input_text_y'].str.len()>0]

In [10]:
# Text preprocess
def preprocess(ds,columns):
    ds = ds.replace(r'\n',' ', regex=True)
#     ds = ds.replace(r'[^\w\s]+', ' ', regex=True)
#     for feature in columns:
#         ds[feature] = ds[feature].str.lower().str.strip()
        
    return ds

columns = ['story', 'input_text_x', 'span_text', 'input_text_y']

train_val_df = preprocess(train_val_df,columns)
test_df = preprocess(test_df,columns)

## [Task 2] Train, Validation and Test splits

CoQA only provides a train and validation set since the test set is hidden for evaluation purposes.

We'll consider the provided validation set as a test set. <br>
$\rightarrow$ Write your own script to:
* Split the train data in train and validation splits (80% train and 20% val)
* Perform splits such that a dialogue appears in one split only! (i.e., split at dialogue level)
* Perform splitting using the following seed for reproducibility: 42

#### Reproducibility Memo

Check back tutorial 2 on how to fix a specific random seed for reproducibility!

In [11]:
# Train/Validation Split
set_reproducibility(42)

train_inds, val_inds = next(GroupShuffleSplit(test_size=.20, n_splits=2, random_state = 42).split(train_val_df, groups=train_val_df['id']))

train_df = train_val_df.iloc[train_inds]
val_df = train_val_df.iloc[val_inds].reset_index()

# Add the histoy_context column to the datasets
train_df = add_history_to_context(train_df)
val_df = add_history_to_context(val_df)
test_df = add_history_to_context(test_df)

Adding the history to each entry of the dataframe...


100%|██████████████████████████████████████████████████████████████████████████████| 5754/5754 [01:05<00:00, 87.43it/s]


History added.
Adding the history to each entry of the dataframe...


100%|██████████████████████████████████████████████████████████████████████████████| 1439/1439 [00:16<00:00, 86.96it/s]


History added.
Adding the history to each entry of the dataframe...


100%|████████████████████████████████████████████████████████████████████████████████| 500/500 [00:05<00:00, 83.67it/s]


History added.


In [12]:
# Checking the Dataframes
print(f'Training set [{train_df.shape}]')
print(f'\tFeatures: {list(train_df.columns)}')
display(train_df.head())
#display(train_df.loc[11:15,['id', 'input_text_x', 'input_text_y', 'span_text']])

print(f'Validation set [{val_df.shape}]')
print(f'\tFeatures: {list(val_df.columns)}')
display(val_df.head())
#display(val_df.loc[11:15,['id', 'input_text_x', 'input_text_y', 'span_text']])

print(f'Test set [{test_df.shape}]')
print(f'\tFeatures: {list(test_df.columns)}')
display(test_df.head())
#display(test_df.loc[11:15,['id', 'input_text_x', 'input_text_y', 'span_text']])

Training set [(85823, 12)]
	Features: ['input_text_x', 'turn_id', 'bad_turn_x', 'source', 'id', 'story', 'span_start', 'span_end', 'span_text', 'input_text_y', 'bad_turn_y', 'history_context']


input_text_x 
 turn_id 
 bad_turn_x 
 source 
 id 
 story 
 span_start 
 span_end 
 span_text 
 input_text_y 
 bad_turn_y 
 history_context 
 
 
 
 
 47030 
 Who is Hannah? 
 1 
 NaN 
 mctest 
 3018q3zvoiqh6tkjkzarysii242ra6 
 Hannah Harvey was a ten year old that had many friends in school. She lived in New York and enjoyed doing gymnastics and playing soccer. One day, Hannah came home from school and her parents greeted her. She knew that something was different by the expressions on their faces. Even Jackson, Hannah's dog, was acting different. Hannah asked why everyone was being so strange. Hannah's father, who was known as Pop, explained to Hannah that his job was forcing him to move. Hannah did not seem to think this was too big of a deal. Then, Hannah's mother explained that they were moving to Kenya. Kenya, she explained, was a place in Africa and life would be very different there. As Hannah began to cry thinking about all of her friends at home, Hannah's mother calmed her with a gentle touch. Jackson began howling as Hannah cried, but was also calmed by Hannah's mother. Hannah spent the next two weeks visiting her friends and saying her goodbyes. She did not know the next time she would be home. She cried very hard when she said goodbye to her best friend, Susan. Susan did not quite understand where Kenya was, but promised to visit Hannah. The next day, Hannah boarded a plane with her family. At first, they thought that Jackson could not come with them. However, Hannah worked hard and helped make sure that he had all of his shots so that he could come. After he had them all, the airport said it was OK for Jackson to come! The Harvey family left and off they went across the ocean to begin their new life in Kenya. 
 18 
 32 
 a ten year old 
 a ten year old 
 NaN 
 Hannah Harvey was a ten year old that had many friends in school. She lived in New York and enjoyed doing gymnastics and playing soccer. One day, Hannah came home from school and her parents greeted her. She knew that something was different by the expressions on their faces. Even Jackson, Hannah's dog, was acting different. Hannah asked why everyone was being so strange. Hannah's father, who was known as Pop, explained to Hannah that his job was forcing him to move. Hannah did not seem to think this was too big of a deal. Then, Hannah's mother explained that they were moving to Kenya. Kenya, she explained, was a place in Africa and life would be very different there. As Hannah began to cry thinking about all of her friends at home, Hannah's mother calmed her with a gentle touch. Jackson began howling as Hannah cried, but was also calmed by Hannah's mother. Hannah spent the next two weeks visiting her friends and saying her goodbyes. She did not know the next time she would be home. She cried very hard when she said goodbye to her best friend, Susan. Susan did not quite understand where Kenya was, but promised to visit Hannah. The next day, Hannah boarded a plane with her family. At first, they thought that Jackson could not come with them. However, Hannah worked hard and helped make sure that he had all of his shots so that he could come. After he had them all, the airport said it was OK for Jackson to come! The Harvey family left and off they went across the ocean to begin their new life in Kenya. 
 
 
 47031 
 Where did she live? 
 2 
 NaN 
 mctest 
 3018q3zvoiqh6tkjkzarysii242ra6 
 Hannah Harvey was a ten year old that had many friends in school. She lived in New York and enjoyed doing gymnastics and playing soccer. One day, Hannah came home from school and her parents greeted her. She knew that something was different by the expressions on their faces. Even Jackson, Hannah's dog, was acting different. Hannah asked why everyone was being so strange. Hannah's father, who was known as Pop, explained to Hannah that his job was forcing him to move. Hannah did not seem to think this was too big of a deal. Then, Hannah's mother explained that they were moving 

Validation set [(21452, 13)]
	Features: ['index', 'input_text_x', 'turn_id', 'bad_turn_x', 'source', 'id', 'story', 'span_start', 'span_end', 'span_text', 'input_text_y', 'bad_turn_y', 'history_context']


index 
 input_text_x 
 turn_id 
 bad_turn_x 
 source 
 id 
 story 
 span_start 
 span_end 
 span_text 
 input_text_y 
 bad_turn_y 
 history_context 
 
 
 
 
 3212 
 17365 
 What sport are they playing? 
 1 
 NaN 
 cnn 
 3018q3zvoiqh6tkjkzarysii34aary 
 (CNN) -- Five-time winner Roger Federer opened his U.S. Open account Monday with a straight sets win over Santiago Giraldo in New York. Despite surrendering his serve three times, the 30-year-old Swiss enjoyed a relatively comfortable style="display:inline" match against the Colombian, ranked 54 in the world, winning 6-4 6-3 6-2 on the Arthur Ashe Stadium court. Leading 5-1 in the opening set, a number of uncharacteristic errors from Federer saw him squander a double-break advantage before he finally rallied to win 6-4. The second and third sets were more straight-forward, though the world number three will be concerned about his winners-to-unforced errors ratio -- he finished with 36 winners and 35 unforced errors. "It was quite up and down, getting used to the conditions," admitted Federer, in quotes carried by usopen.org. "I don't think I've ever played my best in the first round but it's important to come through them and come up with a good feeling." Home favorite Mardy Fish was ruthlessly efficient as he easily dispatched Germany's Tobias Kamke 6-2 6-2 6-1. However fellow American Ryan Harrison was not so fortunate. The 19-year old lost out to big-serving Croat Marin Cilic, 6-2, 7-5, 7-6 (8/6). Seventh seed Gael Monfils ruined the U.S. Open debut of Grigor Dimitrov of Bulgaria with a battling 7-6, 6-3, 6-4 victory, while Czech Tomas Berdych, the number nine seed, beat French qualifier Romain Jouan 6-2, 7-6 (7/4), 6-1. Elsewhere, French 13th seed Richard Gasquet trounced Ukrainian Sergiy Stakhovsky 6-4 6-4 6-0, Serbian Janko Tipsarevic ousted France's Augustin Gensse 6-2 7-5 6-0, while Czech Radek Stepanek beat Germany's Philipp Kohlschreiber 6-4 6-1 6-3. 
 9 
 60 
 Five-time winner Roger Federer opened his U.S. Open 
 tennis 
 NaN 
 (CNN) -- Five-time winner Roger Federer opened his U.S. Open account Monday with a straight sets win over Santiago Giraldo in New York. Despite surrendering his serve three times, the 30-year-old Swiss enjoyed a relatively comfortable style="display:inline" match against the Colombian, ranked 54 in the world, winning 6-4 6-3 6-2 on the Arthur Ashe Stadium court. Leading 5-1 in the opening set, a number of uncharacteristic errors from Federer saw him squander a double-break advantage before he finally rallied to win 6-4. The second and third sets were more straight-forward, though the world number three will be concerned about his winners-to-unforced errors ratio -- he finished with 36 winners and 35 unforced errors. "It was quite up and down, getting used to the conditions," admitted Federer, in quotes carried by usopen.org. "I don't think I've ever played my best in the first round but it's important to come through them and come up with a good feeling." Home favorite Mardy Fish was ruthlessly efficient as he easily dispatched Germany's Tobias Kamke 6-2 6-2 6-1. However fellow American Ryan Harrison was not so fortunate. The 19-year old lost out to big-serving Croat Marin Cilic, 6-2, 7-5, 7-6 (8/6). Seventh seed Gael Monfils ruined the U.S. Open debut of Grigor Dimitrov of Bulgaria with a battling 7-6, 6-3, 6-4 victory, while Czech Tomas Berdych, the number nine seed, beat French qualifier Romain Jouan 6-2, 7-6 (7/4), 6-1. Elsewhere, French 13th seed Richard Gasquet trounced Ukrainian Sergiy Stakhovsky 6-4 6-4 6-0, Serbian Janko Tipsarevic ousted France's Augustin Gensse 6-2 7-5 6-0, while Czech Radek Stepanek beat Germany's Philipp Kohlschreiber 6-4 6-1 6-3. 
 
 
 3213 
 17366 
 What event was it? 
 2 
 NaN 
 cnn 
 3018q3zvoiqh6tkjkzarysii34aary 
 (CNN) -- Five-time winner Roger Federer opened his U.S. Open account Monday with a straight sets win over Santiago Giraldo in New York. Despite surrendering his serve three times, the 30-year-old Sw

Test set [(7917, 10)]
	Features: ['input_text_x', 'turn_id', 'source', 'id', 'story', 'span_start', 'span_end', 'span_text', 'input_text_y', 'history_context']


input_text_x 
 turn_id 
 source 
 id 
 story 
 span_start 
 span_end 
 span_text 
 input_text_y 
 history_context 
 
 
 
 
 5257 
 What's Rubio going to decide in the next few weeks? 
 1 
 cnn 
 3018q3zvoiqh6tkjkzarysii2vbarg 
 (CNN)Sen. Marco Rubio said he'll make a decision on running for president in the next few weeks and feels confident that he could obtain the resources to "credibly run a campaign and win," despite an increasingly crowded GOP field taking shape. In a wide-ranging interview with CNN's Wolf Blitzer, the Florida Republican also gave his thoughts on Republican efforts to defund the president's executive action on immigration, and further explained why he won't support the administration's new Cuba policy. 2016 Rubio, who released a new book "American Dreams" on Tuesday, said he's still deciding whether he thinks he can be more effective as president or as a senator under the new majority. He has already said he won't run for both offices in 2016. Marco Rubio: Radicalized individuals 'very real threat' to the West With power players Mitt Romney and Jeb Bush now considered likely contenders, Rubio said "they're both credible and well-funded" candidates but argued there would still be room for his campaign if he decides to plow forward. "I'm confident that if we decide to run for president ... we will have the funding and the resources necessary to credibly run a campaign and win," he said. "But I understand that the longer you wait, the harder it becomes to do that," he added. Romney tells donors he's considering 2016 bid Bush and Romney have already been in active in talking with big-money supporters and securing financial resources, making it strategically more difficult for other potential contenders like Rubio to lock down support from the GOP's donor class. 
 49 
 74 
 on running for president 
 running for president 
 (CNN)Sen. Marco Rubio said he'll make a decision on running for president in the next few weeks and feels confident that he could obtain the resources to "credibly run a campaign and win," despite an increasingly crowded GOP field taking shape. In a wide-ranging interview with CNN's Wolf Blitzer, the Florida Republican also gave his thoughts on Republican efforts to defund the president's executive action on immigration, and further explained why he won't support the administration's new Cuba policy. 2016 Rubio, who released a new book "American Dreams" on Tuesday, said he's still deciding whether he thinks he can be more effective as president or as a senator under the new majority. He has already said he won't run for both offices in 2016. Marco Rubio: Radicalized individuals 'very real threat' to the West With power players Mitt Romney and Jeb Bush now considered likely contenders, Rubio said "they're both credible and well-funded" candidates but argued there would still be room for his campaign if he decides to plow forward. "I'm confident that if we decide to run for president ... we will have the funding and the resources necessary to credibly run a campaign and win," he said. "But I understand that the longer you wait, the harder it becomes to do that," he added. Romney tells donors he's considering 2016 bid Bush and Romney have already been in active in talking with big-money supporters and securing financial resources, making it strategically more difficult for other potential contenders like Rubio to lock down support from the GOP's donor class. 
 
 
 5258 
 Does he feel confident about it? 
 2 
 cnn 
 3018q3zvoiqh6tkjkzarysii2vbarg 
 (CNN)Sen. Marco Rubio said he'll make a decision on running for president in the next few weeks and feels confident that he could obtain the resources to "credibly run a campaign and win," despite an increasingly crowded GOP field taking shape. In a wide-ranging interview with CNN's Wolf Blitzer, the Florida Republican also gave his thoughts on Republican efforts to defund the president's executive action on immigration, and further explained why he 

Now we check if there is any overlapping dialogue between train and validation set.

In [13]:
set_train = set(train_df['id'])
set_val = set(val_df['id'])

overlap = False
for i in set_train:
    if i in set_val:
        overlap = True
        break

print('Overlap' if overlap else 'No overlap')

No overlap


In [14]:
# Relevant features for the dataset
featurez = ['story', 'input_text_x', 'span_text', 'input_text_y', 'history_context','source']

# Dataframes to Datasets
train_df_to_ds = train_df[featurez]
val_df_to_ds = val_df[featurez]
test_df_to_ds = test_df[featurez]

train_df_to_ds = train_df_to_ds.rename(columns={'input_text_x': 'question', 'story': 'context',\
                                               'input_text_y': 'answer', 'span_text': 'text'})
val_df_to_ds = val_df_to_ds.rename(columns={'input_text_x': 'question', 'story': 'context',\
                                               'input_text_y': 'answer', 'span_text': 'text'})
test_df_to_ds = test_df_to_ds.rename(columns={'input_text_x': 'question', 'story': 'context',\
                                               'input_text_y': 'answer', 'span_text': 'text'})

Now, since the dataset is huge and we are more focused on the reasoning on our choices rather than obtaining the best results, we are going to extract a portion of it.
The next step is gonna be the truncation of the inputs lengths. The pre-trained models that are gonna be tested can process lengths up to 512, that is why our truncation will be at least equal to this value; moreover, we are going to sort the datasets according to the sum of the lengths of the 'context' and 'question' fields together, expecting to truncate the least possible number of examples.

In [15]:
model_checkpoint_M1 = 'distilroberta-base'
# Tokenizer
tokenizer_M1 = AutoTokenizer.from_pretrained(model_checkpoint_M1)
assert isinstance(tokenizer_M1, PreTrainedTokenizerFast)

# Setting the BOS and EOS token
tokenizer_M1.bos_token = tokenizer_M1.cls_token
tokenizer_M1.eos_token = tokenizer_M1.sep_token
check_tokens(tokenizer_M1)

Special tokens:
bos_token: <s>
eos_token: </s>
unk_token: <unk>
sep_token: </s>
pad_token: <pad>
cls_token: <s>
mask_token: <mask>
bos_token: 0
eos_token: 2
unk_token: 3
sep_token: 2
pad_token: 1
cls_token: 0
mask_token: 50264


In [27]:
def tokenize_string(string_1, string_2=None):
    if string_2 is not None:
        tokens = tokenizer_M1(string_1,string_2)
    else:
        tokens = tokenizer_M1(string_1)
    return tokens

story_lengths = [len(tokenizer_M1(x,y)["input_ids"]) for (x,y) in zip(train_val_df['story'],\
                                                               train_val_df['input_text_x'])]
fig_inputs = px.box(list(story_lengths),
                   title="Tokenized Stories and Questions Lengths Distribution")
fig_inputs.show()

Token indices sequence length is longer than the specified maximum sequence length for this model (715 > 512). Running this sequence through the model will result in indexing errors


In [16]:
max_length_input = 512 #min(512,round(np.quantile(list(set(inputs_lengths)), .05))) 
print(f'Max length:{max_length_input}')

Max length:512


In [29]:
answers_lengths = [len(tokenizer_M1(x)["input_ids"]) for x in train_val_df['input_text_y']]

fig_inputs = px.box(list(answers_lengths),
                    title="Tokenized Answers Lengths Distribution", 
                    color_discrete_sequence=['red'])
fig_inputs.show()

In [17]:
max_length_answer = 13
# max_length_answer = round(np.quantile(list(set(outputs_lengths)), .75))
print(f'Max length (upper fence): {max_length_answer}')

Max length (upper fence): 13


In [31]:
import plotly.graph_objs as go
from plotly.subplots import make_subplots

def plot_sources(train_df, val_df):
    sources = train_df["source"].unique()

    fig = make_subplots(rows=1, cols=2, subplot_titles=('Sources of stories in train set', 'Sources of stories in validation set'))

    fig.add_trace(go.Bar(x=train_df["source"].value_counts().index.tolist(), 
                         y=train_df["source"].value_counts().values.tolist(),
                         name='Train Data',
                         marker=dict(color='#1f77b4')), 
                  row=1, col=1)

    fig.add_trace(go.Bar(x=val_df["source"].value_counts().index.tolist(), 
                         y=val_df["source"].value_counts().values.tolist(),
                         name='Validation Data',
                         marker=dict(color='#ff7f0e')), 
                  row=1, col=2)

    fig.update_layout(height=500, width=1300, showlegend=True, 
                      legend=dict(x=0.8, y=1.15, orientation="h"))

    fig.show()

plot_sources(train_df, val_df)

In [18]:
# Datasets Batch split
batch_size = 8
ratio = 5

train_samples = (round(train_df_to_ds.shape[0] * ratio / 100) // batch_size) * batch_size

val_samples = (round(val_df_to_ds.shape[0] * ratio / 100) // batch_size) * batch_size
test_samples = (round(test_df_to_ds.shape[0] * ratio / 100) // batch_size) * batch_size

train_dataset = Dataset.from_dict(train_df_to_ds.iloc[:train_samples])
val_dataset = Dataset.from_dict(val_df_to_ds.iloc[:val_samples])
test_dataset = Dataset.from_dict(test_df_to_ds.iloc[:test_samples])

dataset_COQA = DatasetDict({'train':train_dataset,'validation':val_dataset,'test':test_dataset})
print(dataset_COQA)

DatasetDict({
    train: Dataset({
        features: ['context', 'question', 'text', 'answer', 'history_context', 'source'],
        num_rows: 4288
    })
    validation: Dataset({
        features: ['context', 'question', 'text', 'answer', 'history_context', 'source'],
        num_rows: 1072
    })
    test: Dataset({
        features: ['context', 'question', 'text', 'answer', 'history_context', 'source'],
        num_rows: 392
    })
})


In [19]:
def prepare_features(batch, tokenizer, max_length_input, max_length_answer,history=False,test=False):
    
    if not test:
        truncated_contexts = []
        for context, span, answ in zip(batch['context'], batch['text'], batch['answer']):
            max_length_context = max_length_input - len(answ)
            # Compute the start and end indices of the substring in the string
            start = context.find(span)
            end = start + len(span)

            # Compute the start and end indices of the truncated string
            start = max(0, start - (max_length_context - len(span)) // 2)
            end = min(len(context), end + (max_length_context - len(span)) // 2)

            # Truncate the string to a maximum length of 512, centered around the substring
            truncated_context = context[start:end]
            truncated_contexts.append(truncated_context)
        
    # Tokenize the Question and Context columns
    if history:
        encoded_batch_inputs = tokenizer(
            batch['question'],
            batch['history_context'],
            max_length=max_length_input,
            truncation='only_second',
            padding='max_length',
            return_tensors='pt'        
        )
    else:
        encoded_batch_inputs = tokenizer(
            batch['question'],
            batch['context'],
            max_length=max_length_input,
            truncation='only_second',
            padding='max_length',
            return_tensors='pt'        
        )

    # Tokenize the Answer column
    encoded_batch_labels = tokenizer(
        batch['answer'],
        max_length=max_length_answer,
        padding='max_length',
        truncation=True,
        return_tensors='pt'
    )
    
    encoded_batch_inputs['labels'] = encoded_batch_labels.input_ids

    return encoded_batch_inputs

* [M1] DistilRoBERTa (distilberta-base)

In [20]:
# Tokenizing the Dataset
tokenized_datasets_M1 = DatasetDict()

# Use the `prepare_features` functions
tokenized_datasets_M1['train'] = dataset_COQA['train'].map(
    lambda batch: prepare_features(batch, tokenizer_M1, max_length_input, max_length_answer),
    batched=True,
    batch_size=batch_size,
    remove_columns=dataset_COQA['train'].column_names 
    #remove_columns=[x for x in dataset_COQA['train'].column_names if x != 'source']
)

# Use the `prepare_features` functions
tokenized_datasets_M1['validation'] = dataset_COQA['validation'].map(
    lambda batch: prepare_features(batch, tokenizer_M1, max_length_input, max_length_answer),
    batched=True,
    batch_size=batch_size,
    remove_columns=dataset_COQA['validation'].column_names 
    #remove_columns=[x for x in dataset_COQA['train'].column_names if x != 'source']
)

# Use the `prepare_features` functions
tokenized_datasets_M1['test'] = dataset_COQA['test'].map(
    lambda batch: prepare_features(batch, tokenizer_M1, max_length_input, max_length_answer, test=True),
    batched=True,
    batch_size=batch_size,
    remove_columns=dataset_COQA['test'].column_names 
    #remove_columns=[x for x in dataset_COQA['train'].column_names if x != 'source']
)

print(tokenized_datasets_M1)

  0%|          | 0/536 [00:00<?, ?ba/s]

  0%|          | 0/134 [00:00<?, ?ba/s]

  0%|          | 0/49 [00:00<?, ?ba/s]

DatasetDict({
    train: Dataset({
        features: ['input_ids', 'attention_mask', 'labels'],
        num_rows: 4288
    })
    validation: Dataset({
        features: ['input_ids', 'attention_mask', 'labels'],
        num_rows: 1072
    })
    test: Dataset({
        features: ['input_ids', 'attention_mask', 'labels'],
        num_rows: 392
    })
})


## [Task 3] Model definition

Write your own script to define the following transformer-based models from [huggingface](https://HuggingFace.co/).

* [M1] DistilRoBERTa (distilberta-base)
* [M2] BERTTiny (bert-tiny)

**Note**: Remember to install the ```transformers``` python package!

**Note**: We consider small transformer models for computational reasons!

When loading a pre-trained model into a target model, any layers present in the pre-trained model but not in the target model will be discarded. Conversely, any layers present in the target model but not in the pre-trained model will be initialized according to the initialization strategy of the target model.

This behavior is expected when using pre-trained models, and is due to the fact that the architecture of the target model may differ from that of the pre-trained model. It is important to note that this discrepancy in architecture does not necessarily imply that the target model will perform poorly out of the box. However, it is generally necessary to fine-tune the target model on a downstream task in order to achieve good performance.

* [M1] DistilRoBERTa (distilberta-base)

In [23]:
# Load Model
if load_model:
    model_checkpoint_M1 = 'model_M1_42'
    model_M1 = EncoderDecoderModel.from_pretrained(model_checkpoint_M1)
else:
    model_checkpoint_M1 = 'distilroberta-base'
    model_M1 = EncoderDecoderModel.from_encoder_decoder_pretrained(model_checkpoint_M1, model_checkpoint_M1, tie_encoder_decoder=False)

# Model special tokens
model_M1.config.decoder_start_token_id = tokenizer_M1.cls_token_id
model_M1.config_eos_token_id = tokenizer_M1.sep_token_id
model_M1.config.pad_token_id = tokenizer_M1.pad_token_id
model_M1.config.vocab_size = model_M1.config.encoder.vocab_size

# Model hyperparams
model_M1.config.max_length = max_length_answer
model_M1.config.min_length = 1
model_M1.config.no_repeat_ngram_size = 1
model_M1.config.early_stopping = True
model_M1.config.repetition_penalty= 3.
model_M1.config.num_beams = 8

print(f"Parameters #: {model_M1.num_parameters()}")

model_M1.to(device)

Some weights of the model checkpoint at distilroberta-base were not used when initializing RobertaModel: ['lm_head.dense.bias', 'lm_head.decoder.weight', 'lm_head.layer_norm.bias', 'lm_head.layer_norm.weight', 'lm_head.bias', 'lm_head.dense.weight']
- This IS expected if you are initializing RobertaModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaForCausalLM were not initialized from the model checkpoint at distilroberta-base and are newly initialized: ['roberta.encoder.layer.2.crossattention.self.key.weight', 'roberta.encoder.layer.1.crossattention.self.key.weight', 'roberta.encoder.layer.0.crossattention.sel

Parameters #: 178472025


EncoderDecoderModel(
  (encoder): RobertaModel(
    (embeddings): RobertaEmbeddings(
      (word_embeddings): Embedding(50265, 768, padding_idx=1)
      (position_embeddings): Embedding(514, 768, padding_idx=1)
      (token_type_embeddings): Embedding(1, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): RobertaEncoder(
      (layer): ModuleList(
        (0-5): 6 x RobertaLayer(
          (attention): RobertaAttention(
            (self): RobertaSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): RobertaSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): L

In [24]:
# Load Model
if load_model:
    model_checkpoint_M1_H = 'model_M1_H_42'
    model_M1_H = EncoderDecoderModel.from_pretrained(model_checkpoint_M1_H)
else:
    model_checkpoint_M1 = 'distilroberta-base'
    model_M1_H = EncoderDecoderModel.from_encoder_decoder_pretrained(model_checkpoint_M1, model_checkpoint_M1, tie_encoder_decoder=False)

# Model special tokens
model_M1_H.config.decoder_start_token_id = tokenizer_M1.cls_token_id
model_M1_H.config_eos_token_id = tokenizer_M1.sep_token_id
model_M1_H.config.pad_token_id = tokenizer_M1.pad_token_id
model_M1_H.config.vocab_size = model_M1_H.config.encoder.vocab_size

# Model hyperparams
model_M1_H.config.max_length = max_length_answer
model_M1_H.config.min_length = 1
model_M1_H.config.no_repeat_ngram_size = 1
model_M1_H.config.early_stopping = True
model_M1_H.config.repetition_penalty= 3.
model_M1_H.config.num_beams = 8

print(f"Parameters #: {model_M1_H.num_parameters()}")

model_M1_H.to(device)

Some weights of the model checkpoint at distilroberta-base were not used when initializing RobertaModel: ['lm_head.dense.bias', 'lm_head.decoder.weight', 'lm_head.layer_norm.bias', 'lm_head.layer_norm.weight', 'lm_head.bias', 'lm_head.dense.weight']
- This IS expected if you are initializing RobertaModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaForCausalLM were not initialized from the model checkpoint at distilroberta-base and are newly initialized: ['roberta.encoder.layer.2.crossattention.self.key.weight', 'roberta.encoder.layer.1.crossattention.self.key.weight', 'roberta.encoder.layer.0.crossattention.sel

Parameters #: 178472025


EncoderDecoderModel(
  (encoder): RobertaModel(
    (embeddings): RobertaEmbeddings(
      (word_embeddings): Embedding(50265, 768, padding_idx=1)
      (position_embeddings): Embedding(514, 768, padding_idx=1)
      (token_type_embeddings): Embedding(1, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): RobertaEncoder(
      (layer): ModuleList(
        (0-5): 6 x RobertaLayer(
          (attention): RobertaAttention(
            (self): RobertaSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): RobertaSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): L

## [Task 4] Question generation with text passage $P$ and question $Q$ + [Task 6] Train and evaluate $f_\theta(P, Q)$

**[Task 4]**:
We want to define $f_\theta(P, Q)$. 

Write your own script to implement $f_\theta$ for each model: M1 and M2.

#### Formulation

Consider a dialogue on text passage $P$. 

For each question $Q_i$ at dialogue turn $i$, your model should take $P$ and $Q_i$ and generate $A_i$.

**[Task 6]**:
Write your own script to train and evaluate your $f_\theta(P, Q)$.

#### Instructions

* Perform multiple train/evaluation seed runs: [42, 2022, 1337].$^1$
* Evaluate your models with the following metrics: SQUAD F1-score.$^2$
* Fine-tune each transformer-based models for **3 epochs**.
* Report evaluation SQUAD F1-score computed on the validation and test sets.

$^1$ Remember what we said about code reproducibility in Tutorial 2!

$^2$ You can use ```allennlp``` python package for a quick implementation of SQUAD F1-score: ```from allennlp_models.rc.tools import squad```. 

A dataset collator is a function used in data processing for deep learning models, 
especially in training and evaluation. It collates, or collects, several examples 
from a dataset into a batch and performs operations on the batch, such as padding 
or stacking. This is usually done to make the input data compatible with the model's 
batch size, which is the number of samples processed together in one forward/backward pass. 
The dataset collator takes care of the preprocessing required to format the examples in the batch, 
allowing the data to be efficiently processed by the deep learning framework.

* [M1] DistilRoBERTa (distilberta-base)

In [26]:
# Initialize the data collator
data_collator_M1 = DataCollatorForSeq2Seq(tokenizer=tokenizer_M1, model=model_M1)

epochs = 3

# Training hyperparameters
training_args_M1 = Seq2SeqTrainingArguments(
    output_dir='./M1_Checkpoints',
    evaluation_strategy="epoch",
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size,
    predict_with_generate=True,
    overwrite_output_dir=True,
    fp16=True if device == 'cuda' else False, 
    num_train_epochs = epochs,
    weight_decay=0.01,
    logging_steps=10,
    load_best_model_at_end=True,
    save_total_limit=1
)

# Optimizer and scheduler
optimizer_M1 = AdamW(model_M1.parameters(),lr= 5e-5)
train_steps  = epochs*len(tokenized_datasets_M1['train'])/batch_size
scheduler_M1 = transformers.get_cosine_schedule_with_warmup(optimizer=optimizer_M1,num_warmup_steps=50,num_training_steps=train_steps)
optimizers_M1 = optimizer_M1, scheduler_M1

# Trainer definition
trainer_M1 = Seq2SeqTrainer(
    model=model_M1,
    tokenizer=tokenizer_M1,
    args=training_args_M1,
    compute_metrics=lambda pred: compute_metrics(pred, tokenizer_M1),
    train_dataset=tokenized_datasets_M1['train'],
    eval_dataset=tokenized_datasets_M1['validation'],
    optimizers=optimizers_M1,
    data_collator=DataCollatorForSeq2Seq(tokenizer_M1,model=model_M1)
)

In [27]:
os.environ["WANDB_DISABLED"] = "true"

if not load_model:
    # Start the training
    trainer_M1.train()

***** Running training *****
  Num examples = 4288
  Num Epochs = 3
  Instantaneous batch size per device = 8
  Total train batch size (w. parallel, distributed & accumulation) = 8
  Gradient Accumulation steps = 1
  Total optimization steps = 1608
Automatic Weights & Biases logging enabled, to disable set os.environ["WANDB_DISABLED"] = "true"


Saving model checkpoint to ./M1_Checkpoints\checkpoint-500
Configuration saved in ./M1_Checkpoints\checkpoint-500\config.json
Model weights saved in ./M1_Checkpoints\checkpoint-500\pytorch_model.bin
tokenizer config file saved in ./M1_Checkpoints\checkpoint-500\tokenizer_config.json
Special tokens file saved in ./M1_Checkpoints\checkpoint-500\special_tokens_map.json
Deleting older checkpoint [M1_Checkpoints\checkpoint-500] due to args.save_total_limit
Deleting older checkpoint [M1_Checkpoints\checkpoint-1000] due to args.save_total_limit
Deleting older checkpoint [M1_Checkpoints\checkpoint-1500] due to args.save_total_limit
Deleting older checkpoint [M1_Checkpoints\checkpoint-2000] due to args.save_total_limit
Deleting older checkpoint [M1_Checkpoints\checkpoint-2500] due to args.save_total_limit
Deleting older checkpoint [M1_Checkpoints\checkpoint-3000] due to args.save_total_limit
Deleting older checkpoint [M1_Checkpoints\checkpoint-3500] due to args.save_total_limit
Deleting older c

In [ ]:
if not os.path.exists('model_M1_42'):
    os.makedirs('model_M1_42')

if not load_model:
    trainer_M1.save_model('model_M1_42')

#### Evaluation on the Validation Set

In [35]:
# Create a DataLoader for the dataset using the data collator
test_loader_M1 = torch.utils.data.DataLoader(tokenized_datasets_M1['validation'], 
                                          batch_size=batch_size, 
                                          collate_fn=data_collator_M1)

# Generate answers
generate_answers(test_loader_M1,model_M1,tokenizer_M1,dataset_COQA['validation'])

  1%|▌                                                                                 | 1/134 [00:00<00:59,  2.22it/s]

['What sport are they playing?', 'What event was it?', 'where?', 'Who is the five time winner mentioned?', 'Who does he defeat?', 'how did federer describe the conditions', 'How did he describe his playing', 'who is the home favorite?']
Generated ans: ['15 years', '15 years', '15 years', '15 years', '15 years', '15 years', '15 years', '15 years']
True ans: ['tennis', 'the U.S. Open', 'in New York.', 'Roger Federer', 'Santiago Giraldo', '"It was quite up and down, getting used to the conditions,"', '"I don\'t think I\'ve ever played my best in the first round but it\'s important to come through them and come up with a good feeling."', 'Mardy Fish is']
SQuAD F1 score: [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]


  1%|█▏                                                                                | 2/134 [00:00<00:47,  2.75it/s]

['who is the american?', 'how old is he?', 'did he win?', 'When did Betty start working?', 'What kind of colors does she like to wear?', 'Is Jack interested in fashion?', 'What does he wear in summer?', 'Where has Alice shopped for clothes?']
Generated ans: ['15 years', '15 years', '15 years', 'He was could it to a her', 'He was could it to a her', 'He was could it to a her', 'He was could it to a her', 'He was could it to a her']
True ans: ['Ryan Harrison', '19', 'no', 'This year.', 'Bright', 'No', 'a T-shirt', 'street markets']
SQuAD F1 score: [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]


  2%|█▊                                                                                | 3/134 [00:01<00:44,  2.95it/s]

...

 99%|███████████████████████████████████████████████████████████████████████████████▍| 133/134 [00:41<00:00,  4.24it/s]

['name another place that had an avalanche', 'how far is that from Srinagar?', 'did anyone die in that avalanche?', 'were they all men?', 'how far is 75 miles in kilometers?', 'where did another avalanche occur?', 'where is that located?', 'when did it hit?']
Generated ans: ['14 years', '14 years', '14 years', '14 years', '14 years', '14 years', '14 years', '14 years']
True ans: ['Nayal', '75 miles', 'three people', 'no', '120', 'Gulab Bagh', 'north Kashmir', 'Friday morning']
SQuAD F1 score: [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]


100%|████████████████████████████████████████████████████████████████████████████████| 134/134 [00:41<00:00,  3.22it/s]

['was anyone injured?', 'how many?', 'was anyone killed?', 'how many people were moved from Waltengo Nar and Gulab Bagh?', 'what were they put up in?', "Where was his dad's fishing gear?", 'What type of flying object frightened Alex?', 'According to his dad, did he have a reason to be frightened by it?']
Generated ans: ['14 years', '14 years', '14 years', '14 years', '14 years', 'He was could to a the play.', 'He was could to a the play.', 'He was could to a the play.']
True ans: ['yes', 'Three', 'yes', '300', 'makeshift rescue centers', 'the porch', 'a bat', 'no']
SQuAD F1 score: [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
Mean SQuAD F1-score: 0.013805417236112767


Dataset({
    features: ['context', 'question', 'text', 'answer', 'history_context', 'source', 'generated_answer', 'squad_score'],
    num_rows: 1072
})

#### Evaluation on the Test Set

In [30]:
# Create a DataLoader for the dataset using the data collator
test_loader_M1 = torch.utils.data.DataLoader(tokenized_datasets_M1['test'], 
                                          batch_size=batch_size, 
                                          collate_fn=data_collator_M1)

# Generate answers
dataset_COQA['test'] = generate_answers(test_loader_M1,model_M1,tokenizer_M1,dataset_COQA['test'])

  2%|█▋                                                                                 | 1/49 [00:00<00:24,  1.98it/s]

["What's Rubio going to decide in the next few weeks?", 'Does he feel confident about it?', 'What policy is he not in favor of?', 'What type of people does he think are dangerous to the West?', 'Who are some likely competition to him?', 'Does he think they have a lot of money and credibility?', 'What was the title of his book?', 'When was it released?']
Generated ans: ['to20', 'to15 years', 'to20', 'to20', 'to15 years', 'to15 years', 'to15 years', 'to20']
True ans: ['running for president', 'yes', 'immigration', 'Radicalized individuals', 'Mitt Romney and Jeb Bush', 'yes', 'American Dreams', 'Tuesday']
SQuAD F1 score: [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]


  6%|█████                                                                              | 3/49 [00:00<00:12,  3.64it/s]

["Has he decided if he'd be a better president or senator?", 'What happens the longer you wait?', "When's Romney considering making his own bid?", 'What type of resources are Bush and Romney trying to get?', 'What branch of Chemistry seeks ways to use raw materials to make industrial products?', 'Where do these raw materials originate from?', 'What is chemurgy called today?', "What was Carver's full name?"]
Generated ans: ['to15 years', 'to15 years', 'to15 years', 'to20', '14 years', '14 years', '14 years', '14 years']
True ans: ['not yet', 'the harder it becomes', '2016', 'big-money supporters', 'chemurgy.', 'farm products', 'the science of synthetics', 'George Washington Carver']
SQuAD F1 score: [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
['Was his initial step in his process to analyze parts of plants?', 'To determine what?', 'Did he combine substances to make new things?', 'What did he not care about in regards to the products he made?', 'Where was he a scientist?', 'Did he get offers

  8%|██████▊                                                                            | 4/49 [00:01<00:13,  3.35it/s]

...

['What can you learn from the show?', 'Who scored triple century for his country?', 'Was it the first for his country?', 'Which country he played for?', 'In what sports?', 'Who they were facing?', 'What was the ranking of England then?', 'What runs England needed to avoid innings defeat?']
Generated ans: ['15 years.', '14,000', '14,000', '14,000', '14,000', '14,000', '14,000', '14,000']
True ans: ['team spirit', 'Hashim Amla', 'Yes', 'South Africa', 'Cricket', 'England', 'No.1', '150']
SQuAD F1 score: [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]


 98%|████████████████████████████████████████████████████████████████████████████████▎ | 48/49 [00:14<00:00,  3.68it/s]

['How many wickets were left?', 'What was the score in his stand for third wicket?', 'Who was his partner for that?', 'What was his scored at the stand?', 'What was crying?', 'what did the author feed it?', 'what did the author feed it?', 'then what did the cat do?']
Generated ans: ['14,000', '14,000', '14,000', '14,000', 'He was could to it.', 'He was could to it.', 'He was could to it.', 'He was could to it.']
True ans: ['Six', '377', 'Jacques Kallis', '182', 'a cat', 'yes', 'fish', 'fell asleep']
SQuAD F1 score: [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]


100%|██████████████████████████████████████████████████████████████████████████████████| 49/49 [00:14<00:00,  3.41it/s]

['where was the author?', 'was the father alive by then?', 'how far did the author travel?', 'who did the author check about the cat with?', 'what did he find out?', 'by who?', 'what did he call him?', 'how long has he had him?']
Generated ans: ['He was could to it.', 'He was could to it.', 'He was could to it.', 'He was could to it.', 'He was could to it.', 'He was could to it.', 'He was could to it.', 'He was could to it.']
True ans: ["his father's apartment.", 'no', 'a thousand miles', 'neighbors', 'the cat was abandoned', 'his owner', 'Willis', 'five years']
SQuAD F1 score: [0.0, 0.0, 0.0, 0.0, 0.25, 0.0, 0.0, 0.0]
Mean SQuAD F1-score: 0.005920208576271001


## [Task 5] Question generation with text passage $P$, question $Q$ and dialogue history $H$ + [Task 6] Train and evaluate $f_\theta(P, Q, H)$

**[Task 5]**: We want to define $f_\theta(P, Q, H)$. Write your own script to implement $f_\theta$ for each model: M1 and M2.

#### Formulation

Consider a dialogue on text passage $P$. 

For each question $Q_i$ at dialogue turn $i$, your model should take $P$, $Q_i$, and $H = \{ Q_0, A_0, \dots, Q_{i-1}, A_{i-1} \}$ to generate $A_i$.

**[Task 6]**: Write your own script to train and evaluate your $f_\theta(P, Q, H)$.

#### Instructions

* Perform multiple train/evaluation seed runs: [42, 2022, 1337].$^1$
* Evaluate your models with the following metrics: SQUAD F1-score.$^2$
* Fine-tune each transformer-based models for **3 epochs**.
* Report evaluation SQUAD F1-score computed on the validation and test sets.

$^1$ Remember what we said about code reproducibility in Tutorial 2!

$^2$ You can use ```allennlp``` python package for a quick implementation of SQUAD F1-score: ```from allennlp_models.rc.tools import squad```. 

* [M1] DistilRoBERTa (distilberta-base)

In [55]:
# Tokenizing the Dataset
tokenized_datasets_M1_H = DatasetDict()

# Use the `prepare_features` functions
tokenized_datasets_M1_H['train'] = dataset_COQA['train'].map(
    lambda batch: prepare_features(batch, tokenizer_M1, max_length_input, max_length_answer, history=True),
    batched=True,
    batch_size=batch_size,
    remove_columns=dataset_COQA['train'].column_names 
    #remove_columns=[x for x in dataset_COQA['train'].column_names if x != 'source']
)

# Use the `prepare_features` functions
tokenized_datasets_M1_H['validation'] = dataset_COQA['validation'].map(
    lambda batch: prepare_features(batch, tokenizer_M1, max_length_input, max_length_answer, history=True),
    batched=True,
    batch_size=batch_size,
    remove_columns=dataset_COQA['validation'].column_names 
    #remove_columns=[x for x in dataset_COQA['train'].column_names if x != 'source']
)

# Use the `prepare_features` functions
tokenized_datasets_M1_H['test'] = dataset_COQA['test'].map(
    lambda batch: prepare_features(batch, tokenizer_M1, max_length_input, max_length_answer, history=True, test=True),
    batched=True,
    batch_size=batch_size,
    remove_columns=dataset_COQA['test'].column_names 
    #remove_columns=[x for x in dataset_COQA['train'].column_names if x != 'source']
)

print(tokenized_datasets_M1_H)

100%|█████████████████████████████████████████████████████████████████████████████| 1979/1979 [00:09<00:00, 203.44ba/s]

DatasetDict({
    train: Dataset({
        features: ['input_ids', 'attention_mask', 'labels'],
        num_rows: 85820
    })
    validation: Dataset({
        features: ['input_ids', 'attention_mask', 'labels'],
        num_rows: 21452
    })
    test: Dataset({
        features: ['input_ids', 'attention_mask', 'labels'],
        num_rows: 7916
    })
})


In [58]:
# Initialize the data collator
data_collator_M1_H = DataCollatorForSeq2Seq(tokenizer=tokenizer_M1, model=model_M1_H)

epochs = 3

# Training hyperparameters
training_args_M1_H = Seq2SeqTrainingArguments(
    output_dir='./M1_Checkpoints_H',
    evaluation_strategy="epoch",
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size,
    predict_with_generate=True,
    overwrite_output_dir=True,
    fp16=True if device == 'cuda' else False, 
    num_train_epochs = epochs,
    weight_decay=0.01,
    logging_steps=10,
    load_best_model_at_end=True,
    save_total_limit=1
)
# Optimizer and scheduler
optimizer_M1_H = AdamW(model_M1_H.parameters(),lr= 5e-5)
train_steps  = epochs*len(tokenized_datasets_M1_H['train'])/batch_size
scheduler_M1_H = transformers.get_cosine_schedule_with_warmup(optimizer=optimizer_M1_H,num_warmup_steps=50,num_training_steps=train_steps)
optimizers_M1_H = optimizer_M1_H, scheduler_M1_H

trainer_M1 = Seq2SeqTrainer(
    model=model_M1_H,
    tokenizer=tokenizer_M1,
    args=training_args_M1_H,
    compute_metrics=lambda pred: compute_metrics(pred, tokenizer_M1),
    train_dataset=tokenized_datasets_M1_H['train'],
    eval_dataset=tokenized_datasets_M1_H['validation'],
    optimizers=optimizers_M1_H,
    data_collator=DataCollatorForSeq2Seq(tokenizer_M1,model=model_M1_H)
)

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).
Using the `WAND_DISABLED` environment variable is deprecated and will be removed in v5. Use the --report_to flag to control the integrations used for logging result (for instance --report_to none).


In [59]:
os.environ["WANDB_DISABLED"] = "true"

if not load_model:
    trainer_M1_H.train()

In [60]:
if not os.path.exists('model_M1_H_42'):
    os.makedirs('model_M1_H_42')
    
if not load_model:
    trainer_M1_H.save_model('model_M1_H_42')

#### Evaluation on the Validation Set

In [34]:
# Create a DataLoader for the dataset using the data collator
test_loader_M1_H = torch.utils.data.DataLoader(tokenized_datasets_M1_H['validation'], 
                                          batch_size=batch_size, 
                                          collate_fn=data_collator_M1_H)

# Generate answers
generate_answers(test_loader_M1_H,model_M1_H,tokenizer_M1,dataset_COQA['validation'])

NameError: name 'tokenized_datasets_M1_H' is not defined

#### Evaluation on the Test Set

In [ ]:
# Create a DataLoader for the dataset using the data collator
test_loader_M1_H = torch.utils.data.DataLoader(tokenized_datasets_M1_H['test'], 
                                          batch_size=batch_size, 
                                          collate_fn=data_collator_M1_H)

# Generate answers
generate_answers(test_loader_M1_H,model_M1_H,tokenizer_M1,dataset_COQA['test'],verbose=True)

## [Task 7] Error Analysis

Perform a simple and short error analysis as follows:
* Group dialogues by ```source``` and report the worst 5 model errors for each source (w.r.t. SQUAD F1-score).
* Inspect observed results and try to provide some comments (e.g., do the models make errors when faced with a particular question type?)$^1$

$^1$ Check the [paper](https://arxiv.org/pdf/1808.07042.pdf) for some valuable information about question/answer types (e.g., Table 6, Table 8) 

In [33]:
show_worst_five(dataset_COQA['test'])


Source: cnn


context 
 question 
 answer 
 generated_answer 
 squad_score 
 
 
 
 
 0 
 (CNN)Sen. Marco Rubio said he'll make a decision on running for president in the next few weeks and feels confident that he could obtain the resources to "credibly run a campaign and win," despite an increasingly crowded GOP field taking shape. In a wide-ranging interview with CNN's Wolf Blitzer, the Florida Republican also gave his thoughts on Republican efforts to defund the president's executive action on immigration, and further explained why he won't support the administration's new Cuba policy. 2016 Rubio, who released a new book "American Dreams" on Tuesday, said he's still deciding whether he thinks he can be more effective as president or as a senator under the new majority. He has already said he won't run for both offices in 2016. Marco Rubio: Radicalized individuals 'very real threat' to the West With power players Mitt Romney and Jeb Bush now considered likely contenders, Rubio said "they're both credible and well-funded" candidates but argued there would still be room for his campaign if he decides to plow forward. "I'm confident that if we decide to run for president ... we will have the funding and the resources necessary to credibly run a campaign and win," he said. "But I understand that the longer you wait, the harder it becomes to do that," he added. Romney tells donors he's considering 2016 bid Bush and Romney have already been in active in talking with big-money supporters and securing financial resources, making it strategically more difficult for other potential contenders like Rubio to lock down support from the GOP's donor class. 
 What's Rubio going to decide in the next few weeks? 
 running for president 
 to20 
 0.0 
 
 
 297 
 Asuncion, Paraguay (CNN) -- Paraguay installed new top military commanders, but President Fernando Lugo, who had ordered the change in leadership, was not present for the ceremony. Lugo's absence Thursday morning attracted attention given his administration's silence on the sudden change in the leadership of the country's army, air force and navy. The president's decision to replace the top brass came a day after he publicly dismissed rumors about a military coup. Brig. Gen. Bartolome Ramon Pineda Ortiz was named as the new army commander. Brig. Gen. Hugo Gilberto Aranda Chamorro and Rear Adm. Egberto Emerito Orie Benegas took over the top posts at the air force and navy, respectively. The announcement came from the armed forces, not the president's office. Cibar Benitez, commander of the armed forces, was the only top leader to retain his post. Other changes would be forthcoming in the lower ranks, said Benitez at the swearing-in ceremony, but he denied there was any truth to talk of a coup. Paraguay's history is filled with unstable style="display:inline" transitions of power since it emerged from dictatorship in 1989. Although there hasn't been a coup since that year, there were attempted coups in 1996 and 2000, and President Raul Cubas resigned amid controversy in 1999. The military shakeup is the third since Lugo took office. The former Catholic bishop was elected to a five-year term last year. His victory brought an end to six decades of one-party rule in Paraguay, but the honeymoon did not last long. In April, Lugo admitted that he fathered a child while he was still a priest and that he may have fathered more. The revelation, which came as a shock to most, hurt his political image. Calls for his resignation began, and have continued as Lugo has struggled to push reforms through a majority-opposition legislature. 
 who? 
 Cibar Benitez 
 Republican of the 
 0.0 
 
 
 296 
 Asuncion, Paraguay (CNN) -- Paraguay installed new top military commanders, but President Fernando Lugo, who had ordered the change in leadership, was not present for the ceremony. Lugo's absence Thursday morning attracted attention given his administration's silence on the sudden change in the leadership of the country's arm


Source: race


context 
 question 
 answer 
 generated_answer 
 squad_score 
 
 
 
 
 12 
 George Washington Carver showed that plant life was more than just food for animals and humans. Carver's first step was to analyze plant parts to find out what they were made of. He then combined these simpler isolated substances with other substances to create new products. The branch of chemistry that studies and finds ways to use raw materials from farm products to make industrial products is called chemurgy. Carver was one of the first and greatest chemurgists of all time. Today the science of chemurgy is better known as the science of synthetics . Each day people depend on and use synthetics made from raw materials. All his life Carver battled against the disposal of waste materials, and warned of the growing need to develop substitutes for the natural substances being used up by humans. Carver never cared about getting credit for the new products he created. He never tried to patent his discoveries or get wealthy from them. He turned down many offers to leave Tuskegee Institute to become a scientist in private industry. Thomas Edison, inventor of the electric light, offered him a laboratory in Detroit to carry out food research. When the United States government made him a collaborator in the Mycology and Plant Disease Survey of the Department of Agriculture, he accepted the position with the understanding that he wouldn't leave Tuskegee. An authority on plant disease--especially of the fungus variety--Carver sent hundreds of specimens to the United States Department of Agriculture. At the peak of his career, Carver's fame and influence were known on every continent. 
 What branch of Chemistry seeks ways to use raw materials to make industrial products? 
 chemurgy. 
 14 years 
 0.0 
 
 
 357 
 Running Man is a variety show which is aired in SBS, a famous South Korean TV channel. The show broadcasts on Sunday every week. The translation can be watched on the Internet every Monday. It's very interesting and funny. In the program, everyone should keep running. Here are some information of its hosts and hostess. Liu Zaishi, the main host of the show, is known as National Moderator(,). His friendly, witty and lovely hosting style makes him become one of the most popular hosts and comedians in South Korean. Jin Zhongguo, the strongest man on the show, is known as Sparta-kooks . During the race, he can capture others quickly. But sometimes, he can be very cute. Song Zhixiao, the beautiful actress who is also called Mong Zhi, where "mong" means "confused", because of her facial expressions which makes her seem confused. During the race mission, she is ace because of her superior ability to capture. Young people in Korea love the program very much. Why? Because some South Korean stars will be invited to take part in the race every week . They are divided into several teams with MCs. Many stars have participated in the program, for example, Li Minhao, Girls'Generation , Jin Xiuxian etc. What's more, the program is not only relaxing but also educational--- It teaches people the importance of team spirit. 
 What kind of style does he have? 
 friendly, witty and lovely 
 15 years. 
 0.0 
 
 
 358 
 Running Man is a variety show which is aired in SBS, a famous South Korean TV channel. The show broadcasts on Sunday every week. The translation can be watched on the Internet every Monday. It's very interesting and funny. In the program, everyone should keep running. Here are some information of its hosts and hostess. Liu Zaishi, the main host of the show, is known as National Moderator(,). His friendly, witty and lovely hosting style makes him become one of the most popular hosts and comedians in South Korean. Jin Zhongguo, the strongest man on the show, is known as Sparta-kooks . During the race, he can capture others quickly. But sometimes, he can be very cute. Song Zhixiao, the beautiful actress who is also called Mong Zhi, where "mong" means "confused", becau


Source: mctest


context 
 question 
 answer 
 generated_answer 
 squad_score 
 
 
 
 
 31 
 One morning, Justin woke up very excited. He was excited because it was his birthday. He went downstairs to eat breakfast. When he got downstairs his mom said, "Happy Birthday." "Thank you!" Justin said. "Am I going to have lots of presents?" he asked his mom. "Yes, Justin. When your friends come over for your birthday party you'll get lots!" "Hooray!" Justin said, eating his breakfast. Later that day, Justin's friends came over for his birthday party, and they brought over lots of presents. They ate cake and ice cream. They played games like tag and played with a football. After they were done playing Justin got to open his presents. He saw lots of presents. Red ones, blue ones, tall ones, round ones. "Thank you!" Justin said, as he started to open his presents. He got a basketball, a robot toy, a new bike and some super hero toys! After all of Justin's friends left, Justin fell asleep very fast because of the exciting day he had and he was happy he got all of those nice things. 
 was justin sad? 
 no 
 He was could to it. 
 0.0 
 
 
 133 
 A boy was trying to pick out what instrument that he wanted to play. His parents wanted him to pick a good one because playing an instrument was very important to them. So, the boy went to a music store with his parents. When he got there he didn't know where to start, so the boy walked up to the front and asked the man who worked there for help. First the worker brought the boy to a piano. "No way," said the boy, "that looks way too hard!" The worker laughed at this, and then brought out a guitar. The boy thought that guitars were too popular and wanted to play something that not many other people would play. Finally, the worker brought the boy to the drums. "That's it! That is a cool instrument that I could really get into." However, his mom wasn't so happy with this because she thought that he would be too loud. The boy's dad stepped in and talked her into it because he knew that if the boy liked what he did, he would do way better. Twenty years later, and the boy was the drummer in a band. It the most popular rock band in the world. 
 did the boy think he could do it? 
 no 
 He was could to it. 
 0.0 
 
 
 134 
 A boy was trying to pick out what instrument that he wanted to play. His parents wanted him to pick a good one because playing an instrument was very important to them. So, the boy went to a music store with his parents. When he got there he didn't know where to start, so the boy walked up to the front and asked the man who worked there for help. First the worker brought the boy to a piano. "No way," said the boy, "that looks way too hard!" The worker laughed at this, and then brought out a guitar. The boy thought that guitars were too popular and wanted to play something that not many other people would play. Finally, the worker brought the boy to the drums. "That's it! That is a cool instrument that I could really get into." However, his mom wasn't so happy with this because she thought that he would be too loud. The boy's dad stepped in and talked her into it because he knew that if the boy liked what he did, he would do way better. Twenty years later, and the boy was the drummer in a band. It the most popular rock band in the world. 
 what else did he try? 
 a guitar. 
 He was could to it. 
 0.0 
 
 
 135 
 A boy was trying to pick out what instrument that he wanted to play. His parents wanted him to pick a good one because playing an instrument was very important to them. So, the boy went to a music store with his parents. When he got there he didn't know where to start, so the boy walked up to the front and asked the man who worked there for help. First the worker brought the boy to a piano. "No way," said the boy, "that looks way too hard!" The worker laughed at this, and then brought out a guitar. The boy thought that guitars were too popular and wanted to play something that not many other peop


Source: gutenberg


context 
 question 
 answer 
 generated_answer 
 squad_score 
 
 
 
 
 48 
 CHAPTER XII THE MEETING OF THE GEE EYES When Link Merwell went down again Dave looked at Nat Poole, thinking that lad might possibly attack him. But the dudish fellow was too scared to do anything but back away to a safe distance. "Don--don't you dare to hit me, Porter!" he cried, in a trembling voice. "Don't you dare! If you do I'll tell Doctor Clay!" "If you behave yourself I'll not lay my fingers on you, Nat Poole," was the reply. "Merwell brought this on himself--you know that as well as I do." "He's pretty badly hurt, I fear." "Oh, he'll come around all right," answered Dave. "You had better see to it that he gets to the Hall safely." "Are you going to leave me?" "Yes, I want to find Henshaw and the others." Nat Poole wanted to argue, but he did not dare. Dave waited until Link Merwell sat up and opened his eyes. Then he leaped on the ice-boat and flung off the three skates he found there. "Going away?" mumbled Merwell, when he could speak. "Yes, and after this, Link Merwell, see that you keep a civil tongue in your head," answered Dave, and then he trimmed the sail of the ice-boat, shoved the craft around, and started for the river. Dave was a good deal "worked up," but he had not deemed it wise to let his enemies see it. To be called a "poorhouse rat" had stung him to the quick, and once again when touched on that subject he had found his temper as ungovernable as ever. 
 What is the title of the chapter? 
 The meeting of the gee eyes 
 He could had was would to not a the have it is 
 0.0 
 
 
 253 
 CHAPTER XXXVI THE CHARLATAN UNMASKED There seemed for the next few minutes to be a somewhat singular abstention from any desire to interfere with the two people who stood in the centre of the little group, hand-in-hand. Saton, after his first speech, and after Lois had given him her hands, had turned a little defiantly toward Rochester, who remained, however, unmoved, his elbow resting upon the broad mantelpiece, his face almost expressionless. Vandermere, too, stood on one side and held his peace, though the effort with which he did so was a visible one. Lady Mary looked anxiously towards them. Pauline had shrunk back, as though something in the situation terrified her. Even Saton himself felt that it was the silence before the storm. The courage which he had summoned up to meet a storm of disapproval, began to ebb slowly away in the face of this unnatural silence. It was clear that the onus of further speech was to rest with him. Still retaining Lois' hand, he turned toward Rochester. "You have forbidden me to enter your house, or to hold any communication with your ward until she was of age, Mr. Rochester," he said. "One of your conditions I have obeyed. With regard to the other, I have done as I thought fit. However, to-day she is her own mistress. She has consented to be my wife. I do not need to ask for your consent or approval. If you are not willing that she should be married from your roof, I can take her at once to the Comtesse, who is prepared to receive her." 
 When Saton turned toward Rochester was he defiant or scared? 
 defiant 
 He could had was would to not a be the have it 
 0.0 
 
 
 252 
 CHAPTER XXXVI THE CHARLATAN UNMASKED There seemed for the next few minutes to be a somewhat singular abstention from any desire to interfere with the two people who stood in the centre of the little group, hand-in-hand. Saton, after his first speech, and after Lois had given him her hands, had turned a little defiantly toward Rochester, who remained, however, unmoved, his elbow resting upon the broad mantelpiece, his face almost expressionless. Vandermere, too, stood on one side and held his peace, though the effort with which he did so was a visible one. Lady Mary looked anxiously towards them. Pauline had shrunk back, as though something in the situation terrified her. Even Saton himself felt that it was the silence before the storm. The coura


Source: wikipedia


context 
 question 
 answer 
 generated_answer 
 squad_score 
 
 
 
 
 68 
 Wool is the textile fiber obtained from sheep and other animals, including cashmere and mohair from goats, qiviut from muskoxen, angora from rabbits, and other types of wool from camelids. Wool mainly consists of protein together with a few percent lipids. In this regard it is chemically quite distinct from the more dominant textile, cotton, which is mainly cellulose. Wool is produced by follicles which are small cells located in the skin. These follicles are located in the upper layer of the skin called the epidermis and push down into the second skin layer called the dermis as the wool fibers grow. Follicles can be classed as either primary or secondary follicles. Primary follicles produce three types of fiber: kemp, medullated fibers and true wool fibers. Secondary follicles only produce true wool fibers. Medullated fibers share nearly identical characteristics to hair and are long but lack crimp and elasticity. Kemp fibers are very coarse and shed out. Wool's scaling and crimp make it easier to spin the fleece by helping the individual fibers attach to each other, so they stay together. Because of the crimp, wool fabrics have greater bulk than other textiles, and they hold air, which causes the fabric to retain heat. Wool has a high specific heat coefficient, so it impedes heat transfer in general. This effect has benefited desert peoples, as Bedouins and Tuaregs use wool clothes for insulation. 
 where are follicles located? 
 In the skin. 
 Republican of the town 
 0.0 
 
 
 318 
 The Achaemenid Empire, also called the First Persian Empire, was an empire based in Western Asia, founded by Cyrus the Great. Ranging at its greatest extent from the Balkans and Eastern Europe proper in the west to the Indus Valley in the east, it was one of the largest empires in history, spanning 5.5 million square kilometers, and was larger than any previous empire in history. It is equally notable style="display:inline" for its successful model of a centralised, bureaucratic administration (through satraps under the King of Kings), for building infrastructure such as road systems and a postal system, the use of an official language across its territories, and the development of civil services and a large professional army. The empire's successes inspired similar systems in later empires. It is noted in Western history as the antagonist of the Greek city-states during the Greco-Persian Wars and for the emancipation of the Jewish exiles in Babylon. By the 7th century BC, the Persians had settled in the southwestern portion of the Iranian Plateau in the region of Persis, which came to be their . From this region, Cyrus the Great advanced to defeat the Medes, Lydia, and the Neo-Babylonian Empire, establishing the Achaemenid Empire. Alexander the Great, an avid admirer of Cyrus the Great, conquered most of the empire by 330 BC. Upon his death, most of the empire's former territory came under the rule of the Ptolemaic Kingdom and Seleucid Empire, in addition to other minor territories which gained independence at that time. The Iranian population of the central plateau reclaimed power by the second century BC under the Parthian Empire. 
 And in the west? 
 the Balkans and Eastern Europe 
 Spain of the France 
 0.0 
 
 
 317 
 The Achaemenid Empire, also called the First Persian Empire, was an empire based in Western Asia, founded by Cyrus the Great. Ranging at its greatest extent from the Balkans and Eastern Europe proper in the west to the Indus Valley in the east, it was one of the largest empires in history, spanning 5.5 million square kilometers, and was larger than any previous empire in history. It is equally notable style="display:inline" for its successful model of a centralised, bureaucratic administration (through satraps under the King of Kings), for building infrastructure such as road systems and a postal system, the use of an official language across its ter

# Assignment Evaluation

The following assignment points will be awarded for each task as follows:

* Task 1, Pre-processing $\rightarrow$ 0.5 points.
* Task 2, Dataset Splitting $\rightarrow$ 0.5 points.
* Task 3 and 4, Models Definition $\rightarrow$ 1.0 points.
* Task 5 and 6, Models Training and Evaluation $\rightarrow$ 2.0 points.
* Task 7, Analysis $\rightarrow$ 1.0 points.
* Report $\rightarrow$ 1.0 points.

**Total** = 6 points <br>

We may award an additional 0.5 points for outstanding submissions. 
 
**Speed Bonus** = 0.5 extra points <br>

# Report

We apply the rules described in Assignment 1 regarding the report.
* Write a clear and concise report following the given overleaf template (**max 2 pages**).
* Report validation and test results in a table.$^1$
* **Avoid reporting** code snippets or copy-paste terminal outputs $\rightarrow$ **Provide a clean schema** of what you want to show

# Comments and Organization

Remember to properly comment your code (it is not necessary to comment each single line) and don't forget to describe your work!

Structure your code for readability and maintenance. If you work with Colab, use sections. 

This allows you to build clean and modular code, as well as easy to read and to debug (notebooks can be quite tricky time to time).

# FAQ (READ THIS!)

---

**Question**: Does Task 3 also include data tokenization and conversion step?

**Answer:** Yes! These steps are usually straightforward since ```transformers``` also offers a specific tokenizer for each model.

**Example**: 

```
tokenizer = AutoTokenizer.from_pretrained("bert-base-cased")
encoded_text = tokenizer(text)
%% Alternatively
inputs = tokenizer.tokenize(text, add_special_tokens=True, max_length=min(max_length, 512))
input_ids, attention_mask = inputs['input_ids'], inputs['attention_mask']
```

**Suggestion**: Hugginface's documentation is full of tutorials and user-friendly APIs.

---
---

**Question**: I'm hitting **out of memory error** when training my models, do you have any suggestions?

**Answer**: Here are some common workarounds:

1. Try decreasing the mini-batch size
2. Try applying a different padding strategy (if you are applying padding): e.g. use quantiles instead of maximum sequence length

---
---

# Contact

For any doubt, question, issue or help, you can always contact us at the following email addresses:

Teaching Assistants:

* Andrea Galassi -> a.galassi@unibo.it
* Federico Ruggeri -> federico.ruggeri6@unibo.it

Professor:

* Paolo Torroni -> p.torroni@unibo.it

# The End!

Questions?